# Import

In [220]:
import pandas as pd
import geopandas as gpd
import folium
from branca.element import Figure
import cmasher as cmr

from shapely.geometry import MultiPolygon, Polygon
from scipy.spatial import cKDTree

In [221]:
def create_map():
    m = folium.Map(location = [46.856578, 2.351828], zoom_start = 6)
    return m

In [222]:
gdf = gpd.read_file('data/clean/stats.geojson')

In [211]:
# Add main commune of academie
communes = gpd.read_file('data/clean/communes.geojson')
communes = communes.drop_duplicates('lib_commune', keep='first').copy()

# Formation des académies

In [223]:
# Find the closest commune
schooled = gdf.query('num_schools > 0').copy()
schooled['centroid'] = schooled.centroid

indexor = cKDTree(schooled.centroid.apply(lambda x: (x.x, x.y)).values.tolist())

def find_closest_communes(gdf_src, indexor, schooled):
    gdf = gdf_src.copy()
    
    # Find id of the closest commune
    gdf['closest_point_i'] = gdf.centroid.apply(lambda x: indexor.query((x.x, x.y))[1])
    gdf['closest_code_insee'] = gdf['closest_point_i'].apply(lambda x: schooled.iloc[x].code_insee)
    
    # Add centroids of closest commune
    gdf = gdf.merge(schooled[['code_insee', 'centroid']], left_on='closest_code_insee', right_on='code_insee', how='left', suffixes=('', '_y')).drop('code_insee_y', axis=1).rename({'centroid': 'closest_centroid'}, axis=1)
    gdf = gdf.drop('closest_point_i', axis=1)
    return gdf


gdf_2 = find_closest_communes(gdf, indexor, schooled)

C:\Users\Light\AppData\Local\Temp/ipykernel_11080/2497266745.py:3: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  schooled['centroid'] = schooled.centroid
C:\Users\Light\AppData\Local\Temp/ipykernel_11080/2497266745.py:4: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  indexor = cKDTree(schooled.centroid.apply(lambda x: (x.x, x.y)).values.tolist())
C:\Users\Light\AppData\Local\Temp/ipykernel_11080/2497266745.py:10: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  gdf['closest_point_i'] = gdf.centroid.apply(lambda x: indexor.query((x.x, x.y))[1])


In [207]:
# Give an academy to each row
insee2academie = {row['code_insee']: row['academie'] for _, row in gdf.iterrows() if row['academie'] is not None}
gdf_2['inferred_academie'] = gdf_2['closest_code_insee'].apply(lambda x: insee2academie[x])

In [308]:
# Group communes into academies
reds = cmr.take_cmap_colors('Reds', 100, return_fmt='hex')
seismic = cmr.take_cmap_colors('seismic', 100, return_fmt='hex')
v_max = academies.ratio_birth_school.max()
v_min = academies.ratio_birth_school.min()

def choose_color(value):
    r = value / 120
    r_color = reds[min(int(r * 100) - 1, 99)]
    return r_color
    
cols = ['inferred_academie', 'NAIS', 'num_schools', 'geometry']
academies = gdf_2[cols].dissolve('inferred_academie', aggfunc=sum).reset_index()
academies['ratio_birth_school'] =  academies['NAIS'] / academies['num_schools']
academies['color'] = academies.ratio_birth_school.apply(lambda x: choose_color(x))

In [309]:
# Fix academies' names to join communes using their names (no id available)
d = {
    'Aix-Marseille': 'Marseille', 
    'Corse': 'Ajaccio', 
    'Nancy-Metz': 'Nancy', 
    'Orléans-Tours': 'Tours',
}
academies['commune'] = academies.inferred_academie.apply(lambda x: d[x] if x in d else x)
academies = academies.merge(communes[['lib_commune', 'geometry']], left_on='commune', right_on='lib_commune', how='left', suffixes=('', '_commune'))

In [310]:
# Computes points to localize the cities
academies['point_commune'] = academies.set_geometry('geometry_commune').centroid

C:\Users\Light\AppData\Local\Temp/ipykernel_11080/3463516705.py:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  academies['point_commune'] = academies.set_geometry('geometry_commune').centroid


# Segmentation des communes

In [315]:
# Compute ratios
def compute_stats(gdf):
    gdf_geo = gdf[['closest_code_insee', 'geometry']].dissolve('closest_code_insee')
    gdf = gdf.groupby('closest_code_insee').agg({'lib_commune': 'first', 'num_schools':'sum', 'NAIS':'sum'}).reset_index()
    gdf = gdf_geo.merge(gdf, on='closest_code_insee', how='inner')
    gdf['ratio_birth_school'] = gdf.apply(lambda x: x['NAIS'] / x['num_schools'] if x['num_schools'] > 0 else float('inf'), axis=1)
    return gdf

stats = compute_stats(gdf_2)
stats['centroid'] = stats.centroid

In [362]:
# Select segments
high_ratio = stats.query('ratio_birth_school >= 100')
low_ratio = stats.query('ratio_birth_school < 5')

# Creation de la carte

In [365]:
m = create_map()
reds = cmr.take_cmap_colors('Reds', len(academies), return_fmt='hex')
red_square = 'https://cdn4.iconfinder.com/data/icons/pretty-office-part-5-shadow-style/256/Stop-red.png'
blue_square = 'https://icon-library.com/images/blue-icon-png/blue-icon-png-23.jpg'


def style(row):
    return {
        'color': row['properties']['color'],
        'fillColor': row['properties']['color']
    }

# Add academies
aca_group = folium.FeatureGroup(name='Academies').add_to(m)
zones = folium.GeoJson(data=academies[['inferred_academie', 'NAIS', 'num_schools', 'geometry', 'color']], 
               style_function=style, 
               tooltip=folium.GeoJsonTooltip(fields=('inferred_academie', 'NAIS', 'num_schools',), 
                                             aliases=('Académie', '#Naissances', '#Ecoles'))
              )
aca_group.add_child(zones)
              

# Add marker
communes_group = folium.FeatureGroup(name="Communes").add_to(m)
for _, row in academies.iterrows():
    lon = row['point_commune'].x
    lat = row['point_commune'].y
    icon = folium.Marker(location=[lat, lon], 
                          popup=f'Commune: {row["lib_commune"]}')
    communes_group.add_child(icon)
    

# Add zones with not enough schools
high_group = folium.FeatureGroup(name="Ecoles denses").add_to(m)
for _, row in high_ratio.iterrows():
    lon = row['centroid'].x
    lat = row['centroid'].y
    ic = folium.features.CustomIcon(red_square,
                                    icon_size=(14, 14))
    icon = folium.Marker(location=[lat, lon], 
                         icon=ic,
                          popup=f'Commune: {row["lib_commune"]}, #Naissances: {row["NAIS"]}')
    high_group.add_child(icon)
    
    
# Add zones with too much schools
low_group = folium.FeatureGroup(name="Ecoles peu denses").add_to(m)
for _, row in low_ratio.iterrows():
    lon = row['centroid'].x
    lat = row['centroid'].y
    ic = folium.features.CustomIcon(blue_square,
                                    icon_size=(14, 14))
    icon = folium.Marker(location=[lat, lon], 
                         icon=ic,
                          popup=f'Commune: {row["lib_commune"]}, #Naissances: {row["NAIS"]}')
    low_group.add_child(icon)
    

folium.LayerControl().add_to(m)

fig = Figure(width=1000, height=800)
fig.add_child(m)